# Best Model

In [42]:
%load_ext autoreload
%autoreload 2

import numpy as np

import skorch
import torch
import torch.nn as nn

import gradio as gr

import librosa

from joblib import dump, load

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import LabelEncoder

from resnet import ResNet
from gradio_utils import load_as_librosa, predict_gradio
from dataloading import uniformize, to_numpy
from preprocessing import MfccTransformer, TorchTransform



The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [27]:
# Notebook params
SEED : int = 42
np.random.seed(SEED)
torch.manual_seed(SEED)

# Dataloading params
PATHS: list[str] = [
    "../data/",
    "../new_data/JulienNestor",
    "../new_data/classroom_data",
    "../new_data/class",
    "../new_data/JulienRaph",
]
REMOVE_LABEL: list[str] = [
         "penduleinverse", "pendule", 
         "decollage", "atterrissage",
         "plushaut", "plusbas",
         "etatdurgence",
         "faisunflip", 
         "faisUnFlip", "arreteToi", "etatDurgence",
        #  "tournedroite", "arretetoi", "tournegauche"
]
SAMPLE_RATE: int = 16_000
METHOD: str = "time_stretch"
MAX_TIME: float = 3.0

# Features Extraction params
N_MFCC: int = 64
HOP_LENGHT = 2_048

# 1 - Dataloading

In [28]:
# 1-Dataloading
from dataloading import load_dataset, to_numpy
dataset, uniform_lambda = load_dataset(PATHS,
      remove_label=REMOVE_LABEL,
      sr=SAMPLE_RATE,
      method=METHOD,
      max_time=MAX_TIME
    )

In [29]:
list(dataset["ground_truth"].unique())

['recule',
 'tournedroite',
 'arretetoi',
 'tournegauche',
 'gauche',
 'avance',
 'droite']

In [30]:
# 2-Train and split
from sklearn.model_selection import train_test_split
dataset_train, dataset_test = train_test_split(dataset, random_state=0)

X_train = to_numpy(dataset_train["y_uniform"])
y_train = to_numpy(dataset_train["ground_truth"])
X_test = to_numpy(dataset_test["y_uniform"])
y_test = to_numpy(dataset_test["ground_truth"])

# 2 - Preprocessing

In [31]:
only_mffc_transform = Pipeline(
    steps=[
        ("mfcc", MfccTransformer(N_MFCC=N_MFCC, reshape_output=False, hop_length=HOP_LENGHT)),
        ("torch", TorchTransform())
    ]
)

only_mffc_transform.fit(X_train)

X_train_mfcc_torch = only_mffc_transform.transform(X_train)
X_test_mfcc_torch = only_mffc_transform.transform(X_test)

In [32]:
# Train a LabelEncoder (if needed)
label_encoder = LabelEncoder()
label_encoder.fit(y_train)
y_train_enc = label_encoder.transform(y_train)
y_test_enc = label_encoder.transform(y_test)

# 3 - ResNet

In [33]:
if hasattr(torch, "has_mps") and torch.has_mps:
    device = torch.device("mps")
elif hasattr(torch, "has_cuda") and torch.has_cuda:
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

## 3.1 - nn.Module

In [34]:
# from resnet import ResNet

## 3.2 - Train

In [35]:
# Define net
n_labels = np.unique(dataset.ground_truth).size
net = ResNet(in_channels=1, num_classes=n_labels)

# Define model
model = skorch.NeuralNetClassifier(
    module=net,
    criterion=nn.CrossEntropyLoss(),
    callbacks=[skorch.callbacks.EarlyStopping(monitor="train_loss", patience=25)],
    max_epochs=200,
    lr=0.01,
    batch_size=128,
    train_split=None,
    device=device,
)

model.check_data(X_train_mfcc_torch, y_train_enc)
model.fit(X_train_mfcc_torch, y_train_enc)

print(model.score(X_test_mfcc_torch, y_test_enc))

  epoch    train_loss     dur
-------  ------------  ------
      1        2.8646  0.4461
      2        1.9534  0.4322
      3        1.8164  0.4331
      4        1.6889  0.4318
      5        1.5808  0.4329
      6        1.4659  0.4355
      7        1.2894  0.4285
      8        1.3207  0.4280
      9        1.1546  0.4274
     10        1.0586  0.4287
     11        1.0195  0.4313
     12        0.8246  0.4302
     13        0.7612  0.4330
     14        0.7296  0.4315
     15        0.6690  0.4293
     16        0.6205  0.4291
     17        0.5764  0.4290
     18        0.4839  0.4284
     19        0.4984  0.4314
     20        0.4666  0.4324
     21        0.4132  0.4322
     22        0.4440  0.4300
     23        0.4463  0.4300
     24        0.4075  0.4287
     25        0.3908  0.4282
     26        0.3759  0.4278
     27        0.3612  0.4296
     28        0.3189  0.4281
     29        0.3489  0.4308
     30        0.3308  0.4301
     31        0.3353  0.4299
     32   

In [39]:
from joblib import dump, load

dump(model, './model/model.joblib') 
dump(only_mffc_transform, './model/only_mffc_transform.joblib') 
dump(label_encoder, './model/label_encoder.joblib')
dump(SAMPLE_RATE, "./model/SAMPLE_RATE.joblib")
dump(METHOD, "./model/METHOD.joblib")
dump(MAX_TIME, "./model/MAX_TIME.joblib")
dump(N_MFCC, "./model/N_MFCC.joblib")
dump(HOP_LENGHT, "./model/HOP_LENGHT.joblib")

['./model/HOP_LENGHT.joblib']

In [40]:
model = load('./model/model.joblib') 
only_mffc_transform = load('./model/only_mffc_transform.joblib') 
label_encoder = load('./model/label_encoder.joblib') 
SAMPLE_RATE = load("./model/SAMPLE_RATE.joblib")
METHOD = load("./model/METHOD.joblib")
MAX_TIME = load("./model/MAX_TIME.joblib")
N_MFCC = load("./model/N_MFCC.joblib")
HOP_LENGHT = load("./model/HOP_LENGHT.joblib")

sklearn_model = Pipeline(
            steps=[
                ("mfcc", only_mffc_transform),
                ("model", model)
            ]
        )

uniform_lambda = lambda y, sr: uniformize(y, sr, METHOD, MAX_TIME)

In [43]:
title = r"ResNet 9"

description = r"""
<center>
The resnet9 model was trained to classify drone speech command.
<img src="http://zeus.blanchon.cc/dropshare/modia.png" width=200px>
</center>
"""
article = r"""
- [Deep Residual Learning for Image Recognition](https://arxiv.org/pdf/1512.03385)
"""

demo_men = gr.Interface(
    title = title,
    description = description,
    article = article, 
    fn=lambda data: predict_gradio(
        data=data, 
        uniform_lambda=uniform_lambda, 
        sklearn_model=sklearn_model,
        label_transform=label_encoder,
        target_sr=SAMPLE_RATE),
    inputs = gr.Audio(source="microphone", type="numpy"),
    outputs = gr.Label(),
    # allow_flagging = "manual",
    # flagging_options = ['recule', 'tournedroite', 'arretetoi', 'tournegauche', 'gauche', 'avance', 'droite'],
    # flagging_dir = "./flag/men"
)

: 